In [1]:
import warnings
warnings.filterwarnings('ignore')  # "error", "ignore", "always", "default", "module" or "once"

from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from sklearn.metrics import classification_report
import csv
from textblob import TextBlob
import pandas as pd
import sklearn
from gensim.models.word2vec import Word2Vec
import numpy as np
from nltk.util import ngrams
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, TfidfTransformer
from sklearn.naive_bayes import MultinomialNB
from nltk.stem import PorterStemmer, WordNetLemmatizer
import os
import sys
import re
from os.path import join
import datetime as dt
from scipy.stats.stats import pearsonr
from sklearn.metrics import roc_curve, roc_auc_score, auc
from sklearn.model_selection import StratifiedKFold
import itertools
from string import punctuation
from collections import Counter
from nltk.corpus import stopwords
#from textstat.textstat import *

#data = pd.read_csv("dirty.csv", sep=",", names=["bigot", "offensive", "racists", "extremist", "neutral", "class", "tweet"])
data = pd.read_csv("tweets.csv", sep=",", names=["class", "tweet"])

In [2]:
print (data.shape)

(20217, 2)


In [3]:
print (data)

       class                                              tweet
0          4  RT @Kunal131191: 7. Since some cases of \u2018...
1          4  RT @AskAnshul: In Mysore, Pooja eloped with Ab...
2          3  @MilenaRodban Drivel. The Rohingya are practis...
3          3  RT @resist_terror: @RufusHaybron A genocidal p...
4          3  RT @AgorasBlog: (3) bloodthirsty Fulani herdsm...
5          3  Windsor paper used editorial to declare knife ...
6          1  RT @nobigotry: Trumps administration protectin...
7          4  Explosives used in jihad attack at Afghanistan...
8          3  RT @FoxNews: Activist Linda Sarsour Calls for ...
9          3  RT @YishaiFleisher: That \"Mosque\" is actuall...
10         4  RT @IlliniAD: Great to have #ILLINI great and ...
11         1  #ReligionOfPeace:\nDeath toll in #CarBombings ...
12         3  Daca Daca Daca, Schumer Jihad.  Make no mistak...
13         1  Virginia Convert to Islam Plots Jihad Attack, ...
14         3  RT @AmyMek: MERKEL BANNED 

In [4]:
stop_words = set(stopwords.words('english'))
'''
def split_into_lemmas(tweet):
    
    giant_url_regex = ('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|''[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    tweet = re.sub(giant_url_regex, '', tweet)
    snon1 = '&#[0-9]*;'
    tweet = re.sub(snon1, ' ', tweet)
    snon2 = '&#[0-9]*'
    tweet = re.sub(snon2, ' ', tweet)
    tweet = tweet.lower()  
    tweet = tweet.replace("/", "")
    tweet = tweet.replace("\\", "")
    tweet = tweet.replace("//", "")
    tweet = tweet.replace("u2026", "")
    tweet = tweet.replace("htt", "")
    tweet = tweet.replace("http", "")
    tweet = tweet.replace("u2019", "")
    tweet = tweet.replace("u2014", "")
    tweet = tweet.replace("ud83d", "")
    tweet = tweet.replace("ude0e", "")
    #tweet = tweet.replace("rt", "")
    tweet = tweet.replace("text", "")
    tweet = tweet.replace("truncated", "")
    tweet = tweet.replace("false", "")
    tweet = tweet.replace("entity", "")
    tweet = tweet.replace("hashtags", "")
    tweet = tweet.replace("symbol", "")
    tokens = tweet.split()
    # remove remaining tokens that are not alphabetic
    tokens = [word for word in tokens if word.isalpha()]
    # filter out stop words
    tokens = [w for w in tokens if not w in stop_words]
    # filter out short tokens
    tokens = [word for word in tokens if len(word) > 2]
    return tokens
    #words = TextBlob(tweet).words
    #return [word.lemma for word in words if not word in stop_words]
    #return [word.lemma for word in words]
    #return [word.lemma for word in words if not word in stop_words]
    #return [ps.stem(word) for word in words if not word in stop_words]
    #return [lemma.lemmatize(word) for word in words if not word in stop_words]
    #return ngrams(words, 2)
    #return bigrams(words)'''

def split_into_lemmas(tweet):
    
    giant_url_regex = ('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|''[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    tweet = re.sub(giant_url_regex, '', tweet)
    snon1 = '&#[0-9]*;'
    tweet = re.sub(snon1, ' ', tweet)
    snon2 = '&#[0-9]*'
    tweet = re.sub(snon2, ' ', tweet)
    tweet = tweet.lower()
    tweet = tweet.replace("/", "")
    tweet = tweet.replace("\\", "")
    tweet = tweet.replace("//", "")
    tweet = tweet.replace("u2026", "")
    tweet = tweet.replace("u2019", "")
    tweet = tweet.replace("u2014", "")
    tweet = tweet.replace("ud83d", "")
    tweet = tweet.replace("ude0e", "")
    #tweet = tweet.replace("rt", "")
##    tweet = tweet.replace("text", "")
##    tweet = tweet.replace("truncated", "")
##    tweet = tweet.replace("false", "")
##    tweet = tweet.replace("entity", "")
##    tweet = tweet.replace("tag", "")
##    tweet = tweet.replace("http", "")
##    tweet = tweet.replace("truncate", "")
##    tweet = tweet.replace("truncat", "")
##    tweet = tweet.replace("hash", "")
##    tweet = tweet.replace("hashtags", "")
##    tweet = tweet.replace("symbol", "")
##    
    tweet = re.sub("[^a-zA-Z]"," ",tweet)
    ''' 
    tweet = tweet.replace("0", "")
    tweet = tweet.replace("1", "")
    tweet = tweet.replace("2", "")
    tweet = tweet.replace("3", "")
    tweet = tweet.replace("4", "")
    tweet = tweet.replace("5", "")
    tweet = tweet.replace("6", "")
    tweet = tweet.replace("7", "")
    tweet = tweet.replace("8", "")
    tweet = tweet.replace("9", "")
    '''
    tweet = tweet.replace('\'', '')
    #tweet = tweet.replace(not isalpha(tweet), "")
    #tweet = [row[1].replace('rt', ' ') for row in tweet.iterrows()]
    words = TextBlob(tweet).words
    #return [word.lemma for word in words]
    words = [word for word in words if len(word) > 2]
    words = [word for word in words if word.isalpha()]
    return [word.lemma for word in words if not word in stop_words]
    #return [word.lemma for word in words]
    #return [word.lemma for word in words if not word in stop_words]
    #return [ps.stem(word) for word in words if not word in stop_words]
    #return [lemma.lemmatize(word) for word in words if not word in stop_words]
    #return ngrams(words, 3)
    #return bigrams(words)
    #return words


In [5]:
toks = []

for i in data['tweet']:
    x = split_into_lemmas(i)
    toks.append(x)
    print (x)
    
print (toks)

['kunal', 'since', 'case', 'love', 'jihad', 'taken', 'place', 'help', 'mobile', 'phone', 'check', 'incoming', 'call', 'int']
['askanshul', 'mysore', 'pooja', 'eloped', 'abdul', 'parent', 'alleged', 'abdul', 'drugged', 'pooja', 'amp', 'shown', 'explicit', 'video']
['milenarodban', 'drivel', 'rohingya', 'practising', 'jihad', 'claiming', 'victimhood', 'kosovo', 'amp', 'chechnya']
['resist', 'terror', 'rufushaybron', 'genocidal', 'palestinian', 'killed', 'rfk', 'another', 'genocidal', 'palestinian', 'calling', 'jihad', 'mur']
['agorasblog', 'bloodthirsty', 'fulani', 'herdsman', 'armed', 'violent', 'amp', 'dangerous', 'islamist', 'group', 'amp', 'mass', 'murderer', 'exploit']
['windsor', 'paper', 'used', 'editorial', 'declare', 'knife', 'attack', 'israel', 'sacred', 'duty', 'jihad', 'jewish', 'group', 'nation']
['nobigotry', 'trump', 'administration', 'protecting', 'air', 'jihad', 'woman', 'islam', 'terror', 'maga', 'peace', 'truncated']
['explosive', 'used', 'jihad', 'attack', 'afghanista

['race', 'inspires', 'jihad', 'know', 'already', 'wherever', 'islam', 'go', 'terrorism', 'follows']
['asyounotwish', 'well', 'thats', 'exactly', 'rajput', 'protesting', 'dont', 'want', 'film', 'make', 'feel', 'bad', 'terrorist']
['golansh', 'palestiniantradition', 'would', 'stabber', 'knife', 'ancient', 'sacred', 'religious', 'site', 'thisongoingwarn']
['udc', 'truncated', 'fal']
['jananiq', 'jeannakhoul', 'joe', 'kazzi', 'judebilal', 'jihad', 'khalill', 'nccu', 'truncated', 'false', 'entity', 'hashta']
['jihadwatchrs', 'facebook', 'let', 'muslim', 'repeatedly', 'post', 'video', 'calling', 'jihad', 'violence']
['ahmad', 'shakeel', 'really', 'world', 'doesnt', 'know', 'dividing', 'indian', 'name', 'qabristan', 'amp', 'shamshan', 'ahmad', 'patel']
['qatarileaks', 'extremist', 'mufti', 'sadiq', 'ghariani', 'backed', 'terrorist', 'libyan', 'fighting', 'group', 'permitted', 'cjihad', 'gaddafiu']
['palmerreport', 'hope', 'come', 'back', 'hope', 'mueller', 'warrant', 'hand', 'airport', 'penny

['ikhwannot', 'answer', 'actually', 'simple', 'jihadis', 'come', 'oil', 'rich', 'nation', 'heavy', 'demand', 'engineer']
['iamsladewils', 'justintrudeau', 'sure', 'jihad', 'justin', 'rehabilitate', 'misunderstood', 'po', 'truncated', 'false', 'entity', 'hashtags']
['moebhatha', 'jihad', 'justin', 'country', 'border', 'let', 'back', 'common', 'sense', 'truncated', 'false']
['ntalansky', 'stxstargazer', 'think', 'seen', 'single', 'tweet', 'jihadwatchrs', 'twitter', 'feed', 'last', 'week']
['stacybrewer', 'securefreedom', 'mention', 'mueller', 'listened', 'hamas', 'business', 'cair', 'purged', 'fbi', 'database', 'word']
['islam', 'jihad', 'solicitor', 'muslim', 'attacker', 'say', 'victim', 'would', 'cforgottenu', 'truncate']
['ntalansky', 'motivates', 'islamic', 'jihad', 'nsharia', 'sharia', 'obliges', 'jihad', 'islamic', 'law', 'law', 'land', 'nfollow', 'john']
['govt', 'deed', 'shocker', 'padmavat', 'protestors', 'thrashed', 'like', 'mulayam', 'era', 'anti', 'love', 'jihad', 'brigade']


['female', 'cpalestinianu', 'university', 'student', 'taught', 'view', 'jihad', 'terrorist', 'dalal', 'mughrabi', 'led', 'murder', 'israeli', 'http']
['female', 'palestinian', 'university', 'student', 'taught', 'view', 'jihad', 'terrorist', 'dalal', 'mughrabi', 'led', 'murder']
['supreme', 'court', 'big', 'slap', 'called', 'love', 'jihad', 'lovejihad', 'truncated', 'false', 'entity', 'hashtags', 'text']
['democrat', 'jihad', 'police', 'sends', 'baltimore', 'state', 'anarchy', 'maga', 'truncated', 'false', 'entity']
['lemanvct', 'invasion', 'europe', 'nmasked', 'migrant', 'asylum', 'incoming', 'mass', 'muslim', 'large', 'majority', 'salafist', 'salafists']
['namo', 'satya', 'corrected', 'majoritarian', 'government', 'turn', 'blind', 'eye', 'violence', 'majority', 'hindu', 'lawless', 'mob', 'nam']
['shooting', 'player', 'tara', 'tortured', 'traped', 'love', 'jihad', 'raqibul', 'rahman', 'fake', 'hindu', 'name', 'truncated', 'false', 'entity', 'hasht']
['arabic', 'know', 'jihad', 'nsuarez

['alertigbo', 'fulani', 'army', 'could', 'engineer', 'cattle', 'ranching', 'roaming', 'terrorist', 'take', 'clue', 'persecuting', 'jih']
['reevakhanna', 'promote', 'big', 'way', 'bollywood', 'influenced', 'hindu', 'girl', 'lot', 'love', 'jihad', 'truncated', 'false', 'entity']
['nanner', 'ever', 'since', 'discovered', 'obama', 'admin', 'doh', 'took', 'jihad', 'lexicon', 'amp', 'called', 'vet', 'christian', 'amp', 'right', 'wing', 'terro']
['ever', 'since', 'discovered', 'obama', 'admin', 'doh', 'took', 'jihad', 'lexicon', 'amp', 'called', 'vet', 'christian', 'amp', 'right', 'wing']
['reevakhanna', 'saying', 'positive', 'way', 'look', 'perspective', 'ranveer', 'paired', 'opposite', 'deepika']
['azhar', 'panjody', 'republic', 'still', 'using', 'word', 'love', 'jihad', 'shame', 'republic', 'arnab', 'truncated', 'false', 'entity', 'hashta']
['jarallahghizzi', 'best', 'jihad', 'speak', 'truth', 'court', 'unjust', 'ruler', 'nprophet', 'muhammad', 'pbuhn', 'islamn', 'muhammadn']
['abvp', 'bha

...

['natashafatah', 'justintrudeau', 'nnhow', 'much', 'blood', 'shed', 'life', 'lost', 'trudeau', 'get', 'confronted', 'take', 'responsixe']
['artonfurniture', 'want', 'woman', 'covered', 'animal', 'sight', 'tied', 'tempting']
['omaralghabra', 'nov', 'apologize', 'turning', 'away', 'louis', 'continue', 'promote', 'human', 'right', 'globally', 'musxe']
['samike', 'lot', 'work', 'releasing', 'name', 'itxe', 'called', 'making', 'mentaly', 'ill', 'lone', 'wolf']
['gijoe', 'lincolnske', 'micmac', 'another', 'lot', 'scum', 'canada', 'letting', 'drove', 'animal', 'kind', 'ofxe']
['gijoe', 'lincolnske', 'trudeau', 'doesnxe', 'think', 'called', 'barbaric', 'let', 'sink']
['omaralghabra', 'donxe', 'craw', 'back', 'sewer', 'shit', 'hole', 'came', 'rat', 'faced', 'bastard', 'disgracexe']
['justintrudeau', 'idiot', 'always', 'tweet', 'something', 'seems', 'lacking', 'njobxe']
['mpcelina', 'thousand', 'follower', 'retweetxe', 'like', 'celina', 'nlooks', 'good', 'fxa']
['samike', 'right', 'erasing', 'so

['sevenhundred', 'donxe', 'understand', 'material', 'get']
['senategop', 'disappointed', 'despite', 'exemplary', 'qualification', 'outstanding', 'record', 'many', 'colleague', 'across', 'aixe']
['aaronholtzman', 'exposxc', 'michael', 'moates', 'written', 'help', 'purityjthomas', 'hadassahacohen']
['chuckechaves', 'lolxe']
['coming', 'trump', 'supporter', 'tbh']
['made', 'gag', 'marco', 'rubio', 'good', 'thing', 'left', 'young', 'conservatism', 'let']
['willsommer', 'alex', 'jones', 'called', 'rubio', 'frat', 'boy', 'rubio', 'insisted', 'know', 'jones', 'rubio', 'eventually', 'left', 'telling', 'thexe']
['willsommer', 'heated', 'exchange', 'rubio', 'alex', 'jones', 'senate', 'hallway', 'jones', 'crash', 'rubio', 'interview', 'touch', 'rubio', 'shxe']
['cncn', 'alex', 'jones', 'slug']
['lol', 'rubio', 'took', 'care', 'without', 'even', 'cbeating', 'upxe']
['kpconservative', 'idea', 'woman', 'cneedxe', 'abortion', 'order', 'succeed', 'blatantly', 'sexist', 'idea', 'ever', 'heard', 'nnwome

['inhale', 'good', 'shit', 'exhale', 'bullshit']
['crush', 'bit', 'little', 'bit', 'roll', 'take', 'hit']
['god', 'perfect', 'man', 'man', 'made', 'liquor', 'god', 'made', 'pot']
['short', 'term', 'effect', 'mood', 'altering', 'state', 'sens', 'enhanced', 'reality', 'reased']
['diamondandsilk', 'say', 'whattttt', 'ndem', 'rep', 'tell', 'immigration', 'officer', 'safexe', 'trump', 'longer', 'president', 'httxe']
['prisonplanet', 'asian', 'journalist', 'visit', 'london', 'sample', 'brand', 'multiculturalism', 'nnhis', 'conclusion', 'multiculturalism', 'failexe']
['mendlovitzmark', 'three', 'kid', 'orphan', 'oregon', 'thanks', 'drunk', 'driving', 'illegal', 'alien', 'killed', 'parent', 'sanctuary', 'cxe']
['prisonplanet', 'checkmate', 'bigot']
['prisonplanet', 'female', 'south', 'african', 'journalist', 'threatened', 'gang', 'rape', 'questioning', 'land', 'grab']
['breathtakingly', 'idiotic', 'bogus', 'child', 'molestation', 'case', 'work', 'crusading', 'liberal', 'prosecutor']
['prisonpl

['dvatw', 'pob', 'david', 'feeling', 'left', 'gger', 'want', 'wolf', 'whistle', 'sexually', 'harass', 'might', 'sue', 'discrimination']
['wear', 'cross', 'rosary', 'wear', 'hijab']
['cllrroryfiveash', 'take', 'packed', 'lunch', 'start', 'shit', 'job', 'like', 'rest', 'sensexe']
['westernpattie', 'grew', 'rat', 'skulking', 'bad', 'news']
['curtisschirrma', 'course', 'monitor', 'shop', 'jihad', 'ndid', 'mention', 'ion', 'live', 'morgue']
['sahouraxo', 'spanish', 'government', 'cancelled', 'bomb', 'sale', 'saudi', 'arabia', 'due', 'war', 'crime', 'barbaric', 'regime', 'committinxe']
['talk', 'misogyny', 'sexual', 'harassment', 'actually', 'making', 'feel', 'left', 'fecker', 'ever', 'want', 'sexualxe']
['sadiqkhan', 'metpoliceuk', 'tfl', 'business', 'really', 'though', 'knife', 'crime', 'acid', 'attack', 'city', 'thexe']
['zombie', 'legal', 'party', 'lunatic', 'left', 'islamist', 'hang', 'head', 'shame', 'still', 'vote', 'cult', 'labour', 'nec', 'candidaxe']
['cllrbsilvester', 'pakistani',

['stop', 'breeding', 'lot']
['thetweetofgod', 'donald', 'trump', 'asshole', 'asshole', 'kind', 'asshole', 'asshole', 'look', 'say', 'asshole']
['retweet', 'ixe', 'clog', 'one', 'artery']
['cjokexe', 'account', 'god', 'fuck', 'doubting']
['man', 'prayed', 'sport', 'car', 'big', 'penis', 'sorry', 'pal', 'one', 'got']
['breaking', 'news', 'man', 'said', 'raping', 'kid', 'wrong']
['stop', 'kissing', 'as', 'start', 'raping', 'kid']
['kill', 'name', 'feel', 'like', 'donxe', 'think', 'kill', 'make', 'sad']
['road', 'enlightenment', 'always', 'lead', 'valley', 'moron']
['donald', 'trump', 'point', 'die']
['alien', 'landed', 'today', 'said', 'take', 'leader', 'would', 'utterly', 'humiliated']
['racist', 'like', 'human', 'people']
['son', 'year', 'old', 'still', 'life', 'parent', 'loser']
['apocalypse', 'faster']
['love', 'lebron', 'james', 'named', 'king', 'james', 'bible']
['itxe', 'easy', 'blame', 'people', 'problem']
['ixe', 'serious', 'youxe', 'worst', 'specie', 'ever', 'created', 'made', '

In [6]:
for k in toks:
    print (np.sum(len(k)))

14
14
10
13
14
14
12
12
11
13
14
8
15
12
14
15
12
12
13
10
12
14
10
14
13
10
11
10
12
12
10
14
12
11
18
14
13
10
11
11
11
12
11
10
9
11
13
14
11
12
12
9
5
13
11
11
12
14
12
14
11
12
14
12
13
12
14
11
11
13
9
10
11
11
9
13
10
13
12
13
14
10
12
12
12
13
11
5
13
13
15
13
11
8
12
14
8
11
13
10
10
11
14
10
14
13
13
14
12
14
11
11
9
12
10
9
12
11
8
11
13
10
11
10
12
11
11
10
11
14
14
13
12
13
14
13
11
15
12
10
14
11
11
13
9
13
12
14
13
8
13
8
15
12
11
10
11
8
11
10
10
12
11
11
13
13
14
14
11
14
14
13
11
12
11
12
11
13
10
10
13
9
11
10
12
10
9
12
16
10
10
11
13
9
11
13
16
7
11
14
9
14
14
11
11
10
9
10
10
12
9
13
12
15
14
11
10
10
13
10
12
11
12
12
10
12
10
1
14
14
12
4
12
14
7
14
13
10
12
12
14
14
0
12
10
12
8
12
11
10
13
13
12
10
11
12
11
10
9
12
1
10
14
12
12
12
16
11
13
6
14
15
11
12
14
11
11
13
13
9
12
12
12
10
11
10
13
14
12
13
10
12
14
14
12
12
15
12
11
9
15
13
14
8
10
8
14
11
14
11
10
9
15
12
14
12
14
14
10
10
13
10
10
12
10
12
10
15
19
16
13
11
10
11
11
12
13
8
15
8
14
14
10
13
10
11


10
10
11
14
11
12
12
12
11
12
19
12
10
13
12
10
11
12
13
14
10
9
12
14
14
14
14
13
13
12
11
12
13
17
11
9
12
10
12
11
15
15
12
13
16
16
11
9
14
15
10
16
0
11
17
13
12
13
13
12
11
13
10
10
12
7
10
13
15
12
10
13
10
12
12
13
9
12
8
15
9
9
10
10
13
9
15
10
15
15
11
12
16
8
11
7
12
11
13
9
11
13
10
15
13
14
12
11
11
12
10
11
11
9
12
12
10
12
13
10
10
12
15
14
12
12
12
15
14
12
12
16
14
12
16
11
13
14
11
13
13
11
9
9
11
14
12
11
11
11
10
12
13
13
14
9
9
10
11
16
14
15
12
12
9
15
12
11
13
12
8
7
13
14
11
11
11
7
13
10
8
13
12
10
10
12
13
10
8
13
11
11
14
12
8
12
13
11
12
9
13
11
13
11
16
13
13
11
8
13
11
11
14
10
10
16
10
7
10
9
13
16
10
12
10
15
12
10
12
14
10
13
14
12
11
11
14
14
12
12
10
12
12
10
12
7
13
12
12
13
12
13
11
15
11
11
12
12
12
13
13
12
9
10
12
11
15
10
13
9
14
13
10
13
12
13
11
10
15
11
10
13
16
12
13
12
9
10
11
13
10
12
12
10
13
14
10
11
11
12
15
11
13
9
14
10
12
10
12
10
13
16
12
9
13
13
16
9
11
12
11
11
14
12
14
12
12
13
10
12
7
11
13
13
10
9
11
9
15
14
12
10
14
12
12
12
1

13
14
13
11
12
12
15
12
10
11
12
13
10
15
11
12
15
16
13
14
10
14
15
10
11
10
10
11
10
11
12
12
10
11
12
13
11
11
11
13
14
13
11
10
11
10
16
14
9
15
12
13
9
11
13
10
13
10
12
13
10
12
14
10
10
11
11
14
12
13
14
12
13
11
9
10
14
9
12
13
13
11
13
12
12
11
11
14
15
11
12
12
12
11
13
13
12
13
15
11
13
13
10
8
12
10
10
13
9
9
13
15
11
12
12
14
14
12
12
7
9
12
6
11
6
11
6
11
11
9
12
7
7
7
8
10
8
13
11
8
6
7
9
11
11
5
9
5
12
7
6
10
8
7
11
6
7
11
11
11
7
10
9
10
9
10
10
11
12
10
6
11
5
5
7
2
5
14
4
4
5
4
5
5
3
5
4
4
4
2
5
3
3
4
3
3
3
4
4
4
3
3
3
3
3
3
2
4
4
2
3
3
3
4
4
4
3
3
2
3
4
5
5
4
5
4
3
3
4
5
3
4
4
4
4
2
3
3
3
4
3
3
3
3
3
5
5
5
6
3
3
4
4
4
3
3
4
2
3
3
3
3
5
4
4
4
4
2
5
4
3
3
4
3
3
3
5
3
2
4
5
4
3
3
3
4
5
5
5
5
3
4
4
4
3
4
5
3
4
5
4
4
3
3
3
3
4
3
3
4
4
5
4
5
4
5
3
4
3
4
5
3
5
3
3
6
3
4
4
3
3
4
3
3
3
4
3
4
5
4
3
4
3
4
4
4
3
4
4
4
3
4
3
5
3
3
3
3
4
3
3
4
3
3
4
4
3
5
3
5
2
4
4
4
3
3
4
3
5
4
5
3
4
5
4
3
2
5
3
4
3
3
4
4
5
3
3
4
4
3
3
2
3
3
3
3
5
3
3
4
3
3
3
4
4
3
3
3
3
3
4
5
3
3
3
3
4
3
4
3
2


5
4
15
13
12
5
7
14
5
10
16
5
12
5
16
13
14
16
7
12
5
15
13
5
17
13
9
11
5
14
15
13
13
10
13
10
5
11
12
12
11
15
13
12
12
8
15
16
15
12
18
4
12
10
10
13
11
3
11
13
11
8
14
16
14
11
10
17
4
16
4
16
8
5
13
6
9
5
7
9
14
14
11
7
11
5
8
15
13
13
10
13
7
7
6
5
15
8
17
1
9
10
9
9
11
13
5
5
14
3
16
13
14
5
15
13
16
15
2
5
15
15
12
5
13
5
14
12
5
16
12
9
11
13
5
13
13
1
10
5
4
16
13
13
11
13
14
5
13
13
12
13
4
12
3
3
9
12
12
12
11
11
11
13
11
3
11
11
14
14
14
5
18
15
16
13
15
5
5
7
5
5
11
5
5
8
12
5
11
16
12
9
17
11
12
11
13
15
6
15
17
9
16
5
10
4
4
4
3
17
11
14
14
9
14
14
13
11
12
10
8
12
14
13
11
11
5
12
13
12
11
14
8
8
9
12
7
13
9
12
14
13
13
13
16
5
12
11
12
3
12
5
10
6
4
1
1
10
2
11
10
9
2
11
13
4
2
13
12
12
5
4
5
14
7
10
0
2
13
5
4
6
11
12
12
12
4
2
7
11
10
42
5
13
7
4
12
13
10
6
10
3
10
4
8
8
12
3
10
10
16
13
11
4
12
11
14
10
4
13
2
4
4
12
15
3
6
4
8
0
10
2
10
8
5
11
5
14
8
9
14
0
11
7
1
11
8
4
7
2
10
12
2
12
7
3
13
13
11
11
8
5
3
7
12
8
3
7
12
2
6
5
6
8
9
5
14
14
12
13
2
10
12
12
11
7
1

3
4
12
2
16
3
4
6
16
15
1
10
13
7
3
10
10
13
7
15
5
2
16
2
19
7
8
3
10
12
8
10
2
9
8
4
8
11
4
14
6
11
15
9
4
6
5
8
5
19
4
9
14
13
14
8
16
16
15
10
16
2
9
6
7
6
6
12
2
11
5
14
12
7
12
3
10
9
7
11
7
12
13
13
9
12
14
12
9
7
11
9
10
8
19
12
4
8
2
7
6
8
3
5
3
6
14
5
6
4
9
7
12
13
9
5
10
12
3
9
13
11
9
5
7
4
1
6
10
6
3
4
2
4
10
12
7
11
10
6
8
6
6
13
5
4
4
12
9
14
15
3
5
8
10
4
2
2
3
2
9
4
8
10
2
34
2
8
23
3
23
2
9
5
8
11
2
11
10
8
30
3
11
24
9
3
4
1
4
11
5
11
6
2
33
30
15
8
6
18
18
34
17
13
1
8
14
20
11
23
6
11
11
11
4
4
15
27
10
23
2
5
5
5
7
5
7
15
11
10
9
8
11
7
5
11
14
5
4
7
10
10
6
8
15
12
2
5
7
4
8
11
12
11
11
9
13
11
14
13
7
2
6
11
11
10
12
11
14
12
10
7
13
10
4
12
9
13
13
11
13
12
11
12
10
12
12
11
11
9
15
12
4
10
9
6
8
12
10
13
11
12
11
11
15
4
6
11
9
5
12
9
14
9
12
10
12
13
8
12
12
11
15
15
3
5
14
11
11
14
14
11
8
12
10
11
10
10
13
12
5
11
15
6
14
13
10
9
12
13
11
12
8
9
12
11
12
15
8
12
14
13
9
11
5
9
9
11
12
11
11
13
15
14
13
12
8
5
12
10
10
11
12
9
12
10
13
14
13
8
10
11
11
10
12

9
12
12
14
12
10
12
14
12
13
7
14
7
15
12
12
10
11
10
11
10
12
11
9
8
12
12
12
12
10
12
12
10
8
9
12
12
11
12
11
11
12
13
13
12
12
12
11
12
13
9
5
8
13
9
9
14
9
12
1
8
12
5
11
10
12
11
10
11
12
13
8
12
9
11
11
11
5
11
9
14
13
9
15
13
16
14
11
10
8
12
3
10
15
16
15
13
11
13
12
11
15
11
12
12
12
11
11
5
11
8
12
12
14
12
10
13
10
13
6
12
13
14
8
13
14
13
13
15
10
11
11
13
13
16
12
14
14
9
9
12
16
9
13
15
12
10
14
11
13
14
9
13
13
10
13
13
13
10
10
6
11
11
10
14
12
12
11
13
12
12
9
11
12
12
14
15
13
7
15
15
14
10
10
9
13
10
12
15
14
12
12
9
7
12
14
10
2
12
4
10
8
10
6
7
7
11
6
10
8
16
13
9
11
3
2
9
13
9
8
7
10
5
4
4
2
11
6
3
4
3
5
8
13
3
12
4
8
13
5
11
8
2
4
10
16
15
4
8
14
12
13
7
4
4
3
7
6
15
11
9
4
4
9
13
3
5
5
3
7
7
6
5
4
8
12
13
3
6
9
4
6
3
5
6
4
3
5
5
4
5
8
4
5
8
3
2
10
9
12
6
6
5
12
11
10
3
12
3
10
6
4
12
6
7
8
3
7
6
10
3
3
14
13
11
10
12
12
10
10
11
9
4
9
10
9
5
5
15
11
8
12
8
14
5
12
13
11
10
12
14
13
11
14
10
9
11
11
12
9
10
11
10
10
10
11
10
9
9
10
9
13
7
13
11
7
9
6
10
11
13
13

In [7]:
def split_into_lemmas1(tweet):
    
    giant_url_regex = ('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|''[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    tweet = re.sub(giant_url_regex, '', tweet)
    snon1 = '&#[0-9]*;'
    tweet = re.sub(snon1, ' ', tweet)
    snon2 = '&#[0-9]*'
    tweet = re.sub(snon2, ' ', tweet)
    tweet = tweet.lower()  
    tweet = tweet.replace("/", "")
    tweet = tweet.replace("\\", "")
    tweet = tweet.replace("//", "")
    tweet = tweet.replace("u2026", "")
    tweet = tweet.replace("u2019", "")
    tweet = tweet.replace("u2014", "")
    tweet = tweet.replace("ud83d", "")
    tweet = tweet.replace("ude0e", "")
    #tweet = tweet.replace("rt", "")
    tweet = tweet.replace("text", "")
    tweet = tweet.replace("truncated", "")
    tweet = tweet.replace("false", "")
    tweet = tweet.replace("entity", "")
    tweet = tweet.replace("hashtags", "")
    tweet = tweet.replace("symbol", "")
    tweet = tweet.replace("0", "")
    tweet = tweet.replace("1", "")
    tweet = tweet.replace("2", "")
    tweet = tweet.replace("3", "")
    tweet = tweet.replace("4", "")
    tweet = tweet.replace("5", "")
    tweet = tweet.replace("6", "")
    tweet = tweet.replace("7", "")
    tweet = tweet.replace("8", "")
    tweet = tweet.replace("9", "")
    tweet = tweet.replace('\'', '')
    words = TextBlob(tweet).words
    return [word.lemma for word in words if not word in stop_words]
    #return [word.lemma for word in words]
    #return [word.lemma for word in words if not word in stop_words]
    #return [ps.stem(word) for word in words if not word in stop_words]
    #return [lemma.lemmatize(word) for word in words if not word in stop_words]
    #return ngrams(words, 2)
    #return bigrams(words)

In [8]:
toks1 = []

for i in data['tweet']:
    x = split_into_lemmas1(i)
    toks1.append(x)
    
print (toks1)

[['rt', 'kunal', 'since', 'case', 'ulove', 'jihad', 'taken', 'place', 'help', 'mobile', 'phone', 'check', 'incoming', 'call', 'int'], ['rt', 'askanshul', 'mysore', 'pooja', 'eloped', 'abdul', 'parent', 'alleged', 'abdul', 'drugged', 'pooja', 'amp', 'shown', 'explicit', 'video'], ['milenarodban', 'drivel', 'rohingya', 'practising', 'jihad', 'claiming', 'victimhood', 'kosovo', 'amp', 'chechnya'], ['rt', 'resist_terror', 'rufushaybron', 'genocidal', 'palestinian', 'killed', 'rfk', 'another', 'genocidal', 'palestinian', 'calling', 'jihad', 'mur'], ['rt', 'agorasblog', 'bloodthirsty', 'fulani', 'herdsman', 'armed', 'violent', 'amp', 'dangerous', 'islamist', 'group', 'amp', 'mass', 'murderer', 'exploit'], ['windsor', 'paper', 'used', 'editorial', 'declare', 'knife', 'attack', 'israel', 'usacred', 'duty', 'jihad', 'jewish', 'group', 'nation'], ['rt', 'nobigotry', 'trump', 'administration', 'protecting', 'u', 'air', 'jihad', 'woman', 'islam', 'terror', 'maga', 'peace'], ['explosive', 'used', '

In [9]:
print (len(toks1))

20217


In [10]:
#w2v_model = Word2Vec(toks, size=500, window=5, sg = 1, min_count = 1, iter = 10, workers = Pool()._processes) #, size=500, min_count=1, window=10
w2v_model = Word2Vec(toks, size = 250, sg = 1, window = 5, min_count = 1, iter = 10) # size = 500, sg = 1, window = 5, min_count = 1, iter = 10, workers = Pool()._processes size = embed_dim,  
w2v_model.init_sims(replace=True)
w2v_model.wv.save_word2vec_format('myLSTMTweets.word2vec.bin', binary=False)